### Full of Features

#### Libraries

In [1]:
from sklearn.model_selection import cross_val_score
import numpy as np
import pandas as pd
from collections import defaultdict
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error
from math import sqrt
from catboost import CatBoostRegressor, Pool
import pickle

pd.set_option('display.max_columns', 500)

#### Load Data

In [2]:
data_dir = '/Users/konstantinivanov/Documents/work/PIK/files-pik_digital_day_final'
input_dir = '/Users/konstantinivanov/Documents/work/PIK/input'
output_dir = '/Users/konstantinivanov/Documents/work/PIK/output'
sub_dir = '/Users/konstantinivanov/Documents/work/PIK/sub'

#### Third Month - Matching start_square

In [4]:
train_data_lastmar = pd.read_csv(input_dir + "/train_full_lastmar_.csv")
train_data_apr = pd.read_csv(sub_dir + "/subsub_full_feat_apr.csv")
test_data = pd.read_csv(data_dir + '/test.csv', encoding='cp1251')

In [6]:
train_data_lastmar.shape

(9770, 49)

In [7]:
train_data_lastmar.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-10-01       13109.9   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2017-10-01       19898.4   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2017-10-01        2100.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2017-10-01        9614.9   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-11-01       11947.2   

    value          price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  1124.5  135633.913043    38.00        8     10         34        эконом   
1  1412.3  128492.419825    58.01        9     10         34        эконом   
2   345.0  158237.634409    22.58       10     10         34        эконом   
3   769.4  123250.000000    78.81        8     10         34        эконом   
4   526.7  139420.634921    37.93        9     11         35        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          345    825            0    0       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                0   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да        1800   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                               65357                                 25533   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       18.0        12.0             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  1.4           0.28   
3                                    1.7                  1.4           0.28   
4                                    1.7                  1.4           0.28   

   До парк

In [8]:
train_data_apr.shape

(489, 50)

In [9]:
train_data_apr.head()

Unnamed: 0  id                               bulk_id  spalen       date1  \
0           0   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   
1           1   5  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-04-01   
2           2   6  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-04-01   
3           3   7  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-04-01   
4           4  21  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-04-01   

   start_square        value          price  mean_sq  mean_fl  month  \
0   7736.605399   716.692757  153177.777778    38.00        9      4   
1  12212.256133  1112.321480  143370.813397    57.79        9      4   
2    947.837316   189.787947  179690.000000    24.14        9      4   
3   5952.366717   590.209240  136624.000000    80.63        8      4   
4    168.441482    33.359356  182700.000000    93.60        3      4   

   month_cnt Класс объекта  Количество помещений Огорожена территория  \
0         40        эконом                  1983                  нет   
1         40        эконом                  1983                  нет   
2         40        эконом                  1983                  нет   
3         40        эконом                  1983                  нет   
4         40       комфорт                  1094                  нет   

   Площадь земельного участка Входные группы  Детский сад  Школа  Поликлиника  \
0                        17.0             да          345    825            0   
1                        17.0             да          345    825            0   
2                        17.0             да          345    825            0   
3                        17.0             да          345    825            0   
4                         6.8             да          150    550            0   

   ФОК Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  \
0    0       нет       да         да                  1           1   
1    0       нет       да         да                  1           1   
2    0       нет       да         да                  1           1   
3    0       нет       да         да                  1           1   
4    1       нет       да         да                  1           1   

   Видеонаблюдение Подземная парковка Двор без машин  Машиномест  \
0                0                 да             да        1800   
1                0                 да             да        1800   
2                0                 да             да        1800   
3                0                 да             да        1800   
4                1                 да             да         871   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                                4740                                156205   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       13.0         8.0             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1.40           0.28   
3                                    1.7                 1.40        

In [10]:
test_data

id                               bulk_id  spalen       date1  \
0        0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
1        1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
2        2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
3        3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
4        4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   
5        5  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-04-01   
6        6  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-04-01   
7        7  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-04-01   
8        8  F07BF3C7-C905-E811-893D-00505688958B       2  2018-04-01   
9        9  F07BF3C7-C905-E811-893D-00505688958B       3  2018-04-01   
10      10  F07BF3C7-C905-E811-893D-00505688958B       0  2018-04-01   
11      11  F07BF3C7-C905-E811-893D-00505688958B       1  2018-04-01   
12      12  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-05-01   
13      13  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-05-01   
14      14  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-05-01   
15      15  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-05-01   
16      16  F07BF3C7-C905-E811-893D-00505688958B       2  2018-05-01   
17      17  F07BF3C7-C905-E811-893D-00505688958B       3  2018-05-01   
18      18  F07BF3C7-C905-E811-893D-00505688958B       0  2018-05-01   
19      19  F07BF3C7-C905-E811-893D-00505688958B       1  2018-05-01   
20      20  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-03-01   
21      21  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-04-01   
22      22  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-05-01   
23      23  72B1CAF6-A2DC-E511-9840-001EC9D56418       2  2018-03-01   
24      24  35168781-8F60-E611-9523-001EC9D5643C       3  2018-03-01   
25      25  35168781-8F60-E611-9523-001EC9D5643C       2  2018-03-01   
26      26  A8632090-8F60-E611-9523-001EC9D5643C       3  2018-03-01   
27      27  A8632090-8F60-E611-9523-001EC9D5643C       2  2018-03-01   
28      28  50B329EC-1DE2-E511-B953-001EC9D56418       3  2018-03-01   
29      29  F4BE45B2-AFF2-E611-84D2-001EC9D56418       3  2018-03-01   
...    ...                                   ...     ...         ...   
1787  1787  999F708D-4FE9-E711-B9FF-00505688958B       1  2018-04-01   
1788  1788  999F708D-4FE9-E711-B9FF-00505688958B       2  2018-04-01   
1789  1789  999F708D-4FE9-E711-B9FF-00505688958B       4  2018-04-01   
1790  1790  999F708D-4FE9-E711-B9FF-00505688958B       3  2018-04-01   
1791  1791  AECE8386-7E98-E711-8530-00505688958B       2  2018-04-01   
1792  1792  AECE8386-7E98-E711-8530-00505688958B       1  2018-04-01   
1793  1793  AECE8386-7E98-E711-8530-00505688958B       4  2018-04-01   
1794  1794  AECE8386-7E98-E711-8530-00505688958B       0  2018-04-01   
1795  1795  8CEB3310-63E8-E611-B887-001EC9D5643C       4  2018-05-01   
1796  1796  8CEB3310-63E8-E611-B887-001EC9D5643C       2  2018-05-01   
1797  1797  8CEB3310-63E8-E611-B887-001EC9D5643C       3  2018-05-01   
1798  1798  8CEB3310-63E8-E611-B887-001EC9D5643C       1  2018-05-01   
1799  1799  8CEB3310-63E8-E611-B887-001EC9D5643C       0  2018-05-01   
1800  1800  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       0  2018-05-01   
1801  1801  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       2  2018-05-01   
1802  1802  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       1  2018-05-01   
1803  1803  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       3  2018-05-01   
1804  1804  C0B1362A-C378-E511-B4A4-001EC9D5643C       2  2018-05-01   
1805  1805  C0B1362A-C378-E511-B4A4-001EC9D5643C       3  2018-05-01   
1806  1806  C0B1362A-C378-E511-B4A4-001EC9D5643C       4  2018-05-01   
1807  1807  C0B1362A-C378-E511-B4A4-001EC9D5643C       1  2018-05-01   
1808  1808  999F708D-4FE9-E711-B9FF-00505688958B       0  2018-05-01   
1809  1809  999F708D-4FE9-E711-B9FF-00505688958B       1  2018-05-01   
1810  1810  999F708D-4FE9-E711-B9FF-00505688958B

In [11]:
train_data_apr = train_data_apr[train_data_lastmar.columns]

In [13]:
train_data_apr['fl_mod'] = 2

In [14]:
train_data_lastapr = pd.concat([train_data_lastmar, train_data_apr])

In [15]:
train_data_lastapr.shape

(10259, 49)

In [16]:
train_data_lastapr.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-10-01       13109.9   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2017-10-01       19898.4   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2017-10-01        2100.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2017-10-01        9614.9   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-11-01       11947.2   

    value          price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  1124.5  135633.913043    38.00        8     10         34        эконом   
1  1412.3  128492.419825    58.01        9     10         34        эконом   
2   345.0  158237.634409    22.58       10     10         34        эконом   
3   769.4  123250.000000    78.81        8     10         34        эконом   
4   526.7  139420.634921    37.93        9     11         35        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          345    825            0    0       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                0   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да        1800   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                               65357                                 25533   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       18.0        12.0             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  1.4           0.28   
3                                    1.7                  1.4           0.28   
4                                    1.7                  1.4           0.28   

   До парк

Готовлю данные из апреля

In [17]:
train_data_apr.head()

id                               bulk_id  spalen       date1  start_square  \
0   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   7736.605399   
1   5  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-04-01  12212.256133   
2   6  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-04-01    947.837316   
3   7  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-04-01   5952.366717   
4  21  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-04-01    168.441482   

         value          price  mean_sq  mean_fl  month  month_cnt  \
0   716.692757  153177.777778    38.00        9      4         40   
1  1112.321480  143370.813397    57.79        9      4         40   
2   189.787947  179690.000000    24.14        9      4         40   
3   590.209240  136624.000000    80.63        8      4         40   
4    33.359356  182700.000000    93.60        3      4         40   

  Класс объекта  Количество помещений Огорожена территория  \
0        эконом                  1983                  нет   
1        эконом                  1983                  нет   
2        эконом                  1983                  нет   
3        эконом                  1983                  нет   
4       комфорт                  1094                  нет   

   Площадь земельного участка Входные группы  Детский сад  Школа  Поликлиника  \
0                        17.0             да          345    825            0   
1                        17.0             да          345    825            0   
2                        17.0             да          345    825            0   
3                        17.0             да          345    825            0   
4                         6.8             да          150    550            0   

   ФОК Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  \
0    0       нет       да         да                  1           1   
1    0       нет       да         да                  1           1   
2    0       нет       да         да                  1           1   
3    0       нет       да         да                  1           1   
4    1       нет       да         да                  1           1   

   Видеонаблюдение Подземная парковка Двор без машин  Машиномест  \
0                0                 да             да        1800   
1                0                 да             да        1800   
2                0                 да             да        1800   
3                0                 да             да        1800   
4                1                 да             да         871   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                                4740                                156205   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       13.0         8.0             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1.40           0.28   
3                                    1.7                 1.40           0.28   
4                                    7.0                 0.35

In [18]:
test_data.head()

id                               bulk_id  spalen       date1  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   

           price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  147387.111111    37.99        9      3         39        эконом   
1  138465.811966    57.80        9      3         39        эконом   
2  171589.583333    23.67       10      3         39        эконом   
3  134381.707317    80.46        8      3         39        эконом   
4  153177.777778    38.00        9      4         40        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Спортивная площадка  \
0             да          345    825            0    0                  да   
1             да          345    825            0    0                  да   
2             да          345    825            0    0                  да   
3             да          345    825            0    0                  да   
4             да          345    825            0    0                  да   

  Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  Лифт  \
0       нет       да         да                  1           1     1   
1       нет       да         да                  1           1     1   
2       нет       да         да                  1           1     1   
3       нет       да         да                  1           1     1   
4       нет       да         да                  1           1     1   

  Система мусоротведения  Видеонаблюдение Подземная парковка Двор без машин  \
0             контейнеры                0                 да             да   
1             контейнеры                0                 да             да   
2             контейнеры                0                 да             да   
3             контейнеры                0                 да             да   
4             контейнеры                0                 да             да   

   Машиномест  Площадь пром. зоны в радиусе 500 м  \
0        1800                               65357   
1        1800                               65357   
2        1800                               65357   
3        1800                               65357   
4        1800                               65357   

   Площадь зеленой зоны в радиусе 500 м  До Кремля  До ТТК(км)  \
0                                 25533       18.0        12.0   
1                                 25533       18.0        12.0   
2                                 25533       18.0        12.0   
3                                 25533       18.0        12.0   
4                                 25533       18.0        12.0   

   До Садового(км)  До большой дороги на машине(км)  \
0             16.0                             0.55   
1             16.0                             0.55   
2             16.0                             0.55   
3             16.0                             0.55   
4             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  

In [19]:
set(test_data.date1)

{'2018-03-01', '2018-04-01', '2018-05-01'}

In [20]:
min(train_data_apr.value)

0.0

In [21]:
start_square_04 = train_data_apr[['bulk_id', 'spalen', 'start_square', 'value']]
start_square_04['start_square_next'] = start_square_04['start_square'] - start_square_04['value']
start_square_04 = start_square_04.reset_index().drop(['index', 'start_square', 'value'], axis=1)

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [22]:
for itr in range(len(start_square_04)):
    if start_square_04.start_square_next[itr] < 0:
        start_square_04.start_square_next[itr] = 0

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [23]:
start_square_04

bulk_id  spalen  start_square_next
0    FF3814A9-9F7D-E711-8530-00505688958B       1        7019.912642
1    FF3814A9-9F7D-E711-8530-00505688958B       2       11099.934653
2    FF3814A9-9F7D-E711-8530-00505688958B       0         758.049369
3    FF3814A9-9F7D-E711-8530-00505688958B       3        5362.157477
4    7726CF5A-CC0A-E511-8098-001EC9D56418       3         135.082126
5    72B1CAF6-A2DC-E511-9840-001EC9D56418       2         160.173906
6    35168781-8F60-E611-9523-001EC9D5643C       3        4417.996180
7    35168781-8F60-E611-9523-001EC9D5643C       2           0.000000
8    A8632090-8F60-E611-9523-001EC9D5643C       3        1905.063266
9    A8632090-8F60-E611-9523-001EC9D5643C       2           0.000000
10   F4BE45B2-AFF2-E611-84D2-001EC9D56418       3        2720.743077
11   F4BE45B2-AFF2-E611-84D2-001EC9D56418       4           0.000000
12   F4BE45B2-AFF2-E611-84D2-001EC9D56418       1          34.586330
13   F4BE45B2-AFF2-E611-84D2-001EC9D56418       2          71.148088
14   832FDFD6-AFF2-E611-84D2-001EC9D56418       3        1354.239613
15   832FDFD6-AFF2-E611-84D2-001EC9D56418       2        1789.149260
16   A93667C6-B147-E311-8507-001EC9D5643C       2         144.729010
17   E522EAD5-DA93-E311-8208-001EC9D56418       1           0.000000
18   5C0E0157-C197-E711-8530-00505688958B       0           0.000000
19   5C0E0157-C197-E711-8530-00505688958B       3        1427.034652
20   5C0E0157-C197-E711-8530-00505688958B       1         600.275128
21   5C0E0157-C197-E711-8530-00505688958B       2        1941.749410
22   BC92BE33-C197-E711-8530-00505688958B       3        1605.326888
23   BC92BE33-C197-E711-8530-00505688958B       1         712.754483
24   BC92BE33-C197-E711-8530-00505688958B       2         863.322478
25   67127343-C197-E711-8530-00505688958B       1         602.060337
26   67127343-C197-E711-8530-00505688958B       3        2274.179196
27   67127343-C197-E711-8530-00505688958B       2         913.593197
28   BE6C758E-25F4-E611-84D2-001EC9D56418       2        3257.101144
29   BE6C758E-25F4-E611-84D2-001EC9D56418       1           0.000000
..                                    ...     ...                ...
459  51917AB1-4566-E711-97EC-001EC9D56418       2        3239.200932
460  51917AB1-4566-E711-97EC-001EC9D56418       3        2136.368142
461  9A2B12C5-4566-E711-97EC-001EC9D56418       3        4807.735850
462  9A2B12C5-4566-E711-97EC-001EC9D56418       2        2409.998866
463  9A2B12C5-4566-E711-97EC-001EC9D56418       1        1196.568677
464  9A2B12C5-4566-E711-97EC-001EC9D56418       0         258.369027
465  9A2B12C5-4566-E711-97EC-001EC9D56418       4         890.566784
466  E51769DC-4566-E711-97EC-001EC9D56418       2        1293.467456
467  E51769DC-4566-E711-97EC-001EC9D56418       1         589.515603
468  E51769DC-4566-E711-97EC-001EC9D56418       3        1228.475592
469  E51769DC-4566-E711-97EC-001EC9D56418       4        2386.610755
470  8CEB3310-63E8-E611-B887-001EC9D5643C       4        1313.962903
471  8CEB3310-63E8-E611-B887-001EC9D5643C       2        5923.395526
472  8CEB3310-63E8-E611-B887-001EC9D5643C       1        3896.247204
473  8CEB3310-63E8-E611-B887-001EC9D5643C       3        5505.332178
474  8CEB3310-63E8-E611-B887-001EC9D5643C       0         193.710000
475  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       2         372.425916
476  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       1           0.000000
477  C0B1362A-C378-E511-B4A4-001EC9D5643C       2         432.983268
478  C0B1362A-C378-E511-B4A4-001EC9D5643C       3         280.815355
479  C0B1362A-C378-E511-B4A4-001EC9D5643C       1           4.783570
480  999F708D-4FE9-E711-B9FF-00505688958B       0         841.150183
481  999F708D-4FE9-E711-B9FF-00505688958B       1        9564.380094
482  999F708D-4FE9-E711-B9FF-00505688958B       2       15185.561391
483  999F708D-4FE9-E711-B9FF-00505688958B       4        1261.176242
484  999F708D-4FE9-E711-B9FF-00505688958B       3       22074.000859
485  AECE8386-7E98-E711-8530-005

In [24]:
min(start_square_04.start_square_next)

0.0

Готовлю тестовые данные из мая

In [25]:
test_sub_05 = test_data[test_data['date1']=='2018-05-01']
test_sub_05 = pd.merge(test_sub_05, start_square_04, how='inner', on=['bulk_id', 'spalen'])
test_sub_05 = test_sub_05.rename(index=str, columns={"start_square_next": "start_square"})
test_sub_05['plan'] = test_sub_05['start_square']/test_sub_05['mean_sq']
test_sub_05['plan'] = test_sub_05['plan'].astype(int)

In [26]:
test_sub_05.head()

id                               bulk_id  spalen       date1  \
0  12  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-05-01   
1  13  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-05-01   
2  14  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-05-01   
3  15  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-05-01   
4  22  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-05-01   

           price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  157024.074074    37.85        9      5         41        эконом   
1  145962.371134    57.71        9      5         41        эконом   
2  182391.666667    24.29        9      5         41        эконом   
3  139102.816901    80.59        8      5         41        эконом   
4  182700.000000    93.60        3      5         41       комфорт   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1094                  нет                         6.8   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Спортивная площадка  \
0             да          345    825            0    0                  да   
1             да          345    825            0    0                  да   
2             да          345    825            0    0                  да   
3             да          345    825            0    0                  да   
4             да          150    550            0    1                  да   

  Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  Лифт  \
0       нет       да         да                  1           1     1   
1       нет       да         да                  1           1     1   
2       нет       да         да                  1           1     1   
3       нет       да         да                  1           1     1   
4       нет       да         да                  1           1     1   

  Система мусоротведения  Видеонаблюдение Подземная парковка Двор без машин  \
0             контейнеры                0                 да             да   
1             контейнеры                0                 да             да   
2             контейнеры                0                 да             да   
3             контейнеры                0                 да             да   
4             контейнеры                1                 да             да   

   Машиномест  Площадь пром. зоны в радиусе 500 м  \
0        1800                               65357   
1        1800                               65357   
2        1800                               65357   
3        1800                               65357   
4         871                                4740   

   Площадь зеленой зоны в радиусе 500 м  До Кремля  До ТТК(км)  \
0                                 25533       18.0        12.0   
1                                 25533       18.0        12.0   
2                                 25533       18.0        12.0   
3                                 25533       18.0        12.0   
4                                156205       13.0         8.0   

   До Садового(км)  До большой дороги на машине(км)  \
0             16.0                             0.55   
1             16.0                             0.55   
2             16.0                             0.55   
3             16.0                             0.55   
4             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1

In [27]:
test_sub_05['value'] = 0
test_sub_05.drop(['Система мусоротведения', 'Лифт', 'Спортивная площадка'], axis=1, inplace=True)
test_sub_05['fl_mod'] = 2
test_sub_05.to_csv(input_dir + "/test_full_may_.csv", index=False, columns = train_data_lastapr.columns)

train_data_lastapr.to_csv(input_dir + "/train_full_lastapr_.csv", index=False)

#### Validation

In [3]:
TEST_FILE = input_dir + '/test_full_may_.csv' #add
CD_FILE = input_dir + '/train_full_feat.txt'

train_data = pd.read_csv(input_dir + "/train_full_lastapr_.csv")
test_data = pd.read_csv(TEST_FILE)

In [4]:
test_data.head()

id                               bulk_id  spalen       date1  start_square  \
0  12  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-05-01   7019.912642   
1  13  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-05-01  11099.934653   
2  14  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-05-01    758.049369   
3  15  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-05-01   5362.157477   
4  22  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-05-01    135.082126   

   value          price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0      0  157024.074074    37.85        9      5         41        эконом   
1      0  145962.371134    57.71        9      5         41        эконом   
2      0  182391.666667    24.29        9      5         41        эконом   
3      0  139102.816901    80.59        8      5         41        эконом   
4      0  182700.000000    93.60        3      5         41       комфорт   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1094                  нет                         6.8   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          150    550            0    1       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                1   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да         871   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                                4740                                156205   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       13.0         8.0             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1.40           0.28   
3                                    1.7                 1.40           0.28   
4                                    7.0                 0.35           0.45   

   До парка(км) 

In [5]:
train_data.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-10-01       13109.9   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2017-10-01       19898.4   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2017-10-01        2100.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2017-10-01        9614.9   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-11-01       11947.2   

    value          price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  1124.5  135633.913043    38.00        8     10         34        эконом   
1  1412.3  128492.419825    58.01        9     10         34        эконом   
2   345.0  158237.634409    22.58       10     10         34        эконом   
3   769.4  123250.000000    78.81        8     10         34        эконом   
4   526.7  139420.634921    37.93        9     11         35        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          345    825            0    0       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                0   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да        1800   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                               65357                                 25533   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       18.0        12.0             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  1.4           0.28   
3                                    1.7                  1.4           0.28   
4                                    1.7                  1.4           0.28   

   До парк

In [6]:
K = 10

kf = KFold(n_splits=K, random_state=42, shuffle=True)
kf.get_n_splits(range(len(train_data)))

print(kf)  

for i, (train_index, valid_index) in enumerate(kf.split(range(len(train_data)))):
    train = train_data.loc[train_index]
    valid = train_data.loc[valid_index]

    train.to_csv(input_dir + f"/train_{i}.csv",index=False)
    valid.to_csv(input_dir + f"/valid_{i}.csv",index=False)

KFold(n_splits=10, random_state=42, shuffle=True)


#### Fit and Predict

In [7]:
test_pool = Pool(TEST_FILE, column_description=CD_FILE, has_header=True, delimiter=",")

In [8]:
iterations = 5000
learning_rate = 0.05
depth = 8
random_seed = 42

Regressors = [
    CatBoostRegressor(iterations=iterations, learning_rate=learning_rate, depth=depth, random_seed=random_seed)
]

In [9]:
def FitOnKFolds(model):
    cum_y_test = np.zeros((len(test_data), 1))
    pred_y_train = np.zeros((len(train_data), 1))
    
    for i in range(K):
        TRAIN_FILE = input_dir + f'/train_{i}.csv'
        VAL_FILE = input_dir + f'/valid_{i}.csv'
        
        train_pool = Pool(TRAIN_FILE, column_description=CD_FILE, has_header=True, delimiter=",")
        val_pool = Pool(VAL_FILE, column_description=CD_FILE, has_header=True, delimiter=",")
        
        model.fit(train_pool, eval_set = val_pool)
        pickle.dump(model, open(input_dir + f'mod_full_feat_lastapr_{i}.sav', 'wb'))
        
        pred = model.predict(test_pool)
        cum_y_test += pred.reshape((len(test_data),1))
        
        pred = model.predict(val_pool)
        df = pd.read_csv(VAL_FILE)
        pred_y_train[df.id] = pred.reshape((len(df),1))
        
    return (cum_y_test/K).clip(int(min(train_data.value)), int(max(train_data.value))).reshape(-1),\
        sqrt(mean_squared_error(list(train_data['value']), list(pred_y_train)))

In [10]:
def write_ans(fl_name, y_test):
    dict_ans = defaultdict(list)
    dict_ans['id'] = list(range(len(y_test)))
    dict_ans['value'] = list(y_test)
    df_ans = pd.DataFrame.from_dict(dict_ans)
    df_ans.to_csv(sub_dir+'/'+fl_name+'.csv', index=False)
    return 'Answer /%s succesfully writed' % fl_name

In [11]:
%%time

vec_qual = []

for itr, model in enumerate(Regressors):
    y_test, qual = FitOnKFolds(model)
    vec_qual.append(qual)
    write_ans(f'sub_may_ctb_itr={iterations}_lr={learning_rate}_depth={depth}_fld={K}_{itr}vers', y_test)

0:	learn: 423.9078602	test: 420.5851538	best: 420.5851538 (0)	total: 124ms	remaining: 10m 22s
1:	learn: 413.0324330	test: 409.6492396	best: 409.6492396 (1)	total: 173ms	remaining: 7m 13s
2:	learn: 401.8056226	test: 398.5373756	best: 398.5373756 (2)	total: 228ms	remaining: 6m 20s
3:	learn: 391.9444399	test: 389.0768876	best: 389.0768876 (3)	total: 281ms	remaining: 5m 50s
4:	learn: 382.2031736	test: 379.4679144	best: 379.4679144 (4)	total: 335ms	remaining: 5m 34s
5:	learn: 373.1527428	test: 370.3217092	best: 370.3217092 (5)	total: 394ms	remaining: 5m 27s
6:	learn: 365.2713333	test: 362.9694775	best: 362.9694775 (6)	total: 448ms	remaining: 5m 19s
7:	learn: 357.5029983	test: 355.1374922	best: 355.1374922 (7)	total: 475ms	remaining: 4m 56s
8:	learn: 350.5842676	test: 348.1091288	best: 348.1091288 (8)	total: 522ms	remaining: 4m 49s
9:	learn: 344.1517199	test: 341.8752527	best: 341.8752527 (9)	total: 582ms	remaining: 4m 50s
10:	learn: 337.7289764	test: 335.5043252	best: 335.5043252 (10)	total

90:	learn: 220.4215373	test: 234.3041827	best: 234.3041827 (90)	total: 5.05s	remaining: 4m 32s
91:	learn: 219.7892220	test: 233.8130994	best: 233.8130994 (91)	total: 5.12s	remaining: 4m 33s
92:	learn: 219.2246037	test: 233.5121951	best: 233.5121951 (92)	total: 5.2s	remaining: 4m 34s
93:	learn: 218.9017209	test: 233.3581710	best: 233.3581710 (93)	total: 5.25s	remaining: 4m 34s
94:	learn: 218.5138136	test: 232.9196232	best: 232.9196232 (94)	total: 5.32s	remaining: 4m 34s
95:	learn: 218.0205977	test: 232.4496007	best: 232.4496007 (95)	total: 5.38s	remaining: 4m 34s
96:	learn: 217.5919365	test: 231.9943298	best: 231.9943298 (96)	total: 5.45s	remaining: 4m 35s
97:	learn: 217.0980006	test: 231.1965873	best: 231.1965873 (97)	total: 5.5s	remaining: 4m 35s
98:	learn: 216.5699084	test: 230.9664764	best: 230.9664764 (98)	total: 5.56s	remaining: 4m 35s
99:	learn: 215.9960320	test: 230.6618641	best: 230.6618641 (99)	total: 5.61s	remaining: 4m 34s
100:	learn: 215.8799303	test: 230.5710409	best: 230.

178:	learn: 192.3366798	test: 214.2859169	best: 214.2798329 (175)	total: 9.95s	remaining: 4m 28s
179:	learn: 192.0515577	test: 214.2602255	best: 214.2602255 (179)	total: 10s	remaining: 4m 27s
180:	learn: 191.8518222	test: 214.1287930	best: 214.1287930 (180)	total: 10.1s	remaining: 4m 27s
181:	learn: 191.7945384	test: 214.1014803	best: 214.1014803 (181)	total: 10.1s	remaining: 4m 26s
182:	learn: 191.5210097	test: 213.9330379	best: 213.9330379 (182)	total: 10.1s	remaining: 4m 26s
183:	learn: 191.2829649	test: 213.7915145	best: 213.7915145 (183)	total: 10.2s	remaining: 4m 26s
184:	learn: 191.0139463	test: 213.7120242	best: 213.7120242 (184)	total: 10.3s	remaining: 4m 26s
185:	learn: 190.9347000	test: 213.6078690	best: 213.6078690 (185)	total: 10.3s	remaining: 4m 27s
186:	learn: 190.6226029	test: 213.3906222	best: 213.3906222 (186)	total: 10.4s	remaining: 4m 26s
187:	learn: 190.3758496	test: 213.1207852	best: 213.1207852 (187)	total: 10.4s	remaining: 4m 26s
188:	learn: 190.3526997	test: 21

265:	learn: 174.7707504	test: 202.7492458	best: 202.7492458 (265)	total: 14.5s	remaining: 4m 18s
266:	learn: 174.7008725	test: 202.5634995	best: 202.5634995 (266)	total: 14.6s	remaining: 4m 18s
267:	learn: 174.5749390	test: 202.4326342	best: 202.4326342 (267)	total: 14.6s	remaining: 4m 17s
268:	learn: 174.4602283	test: 202.2888784	best: 202.2888784 (268)	total: 14.7s	remaining: 4m 17s
269:	learn: 174.3793731	test: 202.1946992	best: 202.1946992 (269)	total: 14.7s	remaining: 4m 17s
270:	learn: 174.2109929	test: 202.0482465	best: 202.0482465 (270)	total: 14.8s	remaining: 4m 17s
271:	learn: 174.1670772	test: 201.9062176	best: 201.9062176 (271)	total: 14.8s	remaining: 4m 17s
272:	learn: 174.0487789	test: 201.8296573	best: 201.8296573 (272)	total: 14.9s	remaining: 4m 17s
273:	learn: 173.9871654	test: 201.8551915	best: 201.8296573 (272)	total: 14.9s	remaining: 4m 17s
274:	learn: 173.8984959	test: 201.8442064	best: 201.8296573 (272)	total: 15s	remaining: 4m 17s
275:	learn: 173.8408060	test: 20

351:	learn: 164.2164136	test: 195.4737691	best: 195.4737691 (351)	total: 19.3s	remaining: 4m 14s
352:	learn: 164.1382909	test: 195.4603350	best: 195.4603350 (352)	total: 19.3s	remaining: 4m 14s
353:	learn: 164.1214516	test: 195.3540805	best: 195.3540805 (353)	total: 19.4s	remaining: 4m 14s
354:	learn: 164.0872201	test: 195.3490582	best: 195.3490582 (354)	total: 19.4s	remaining: 4m 14s
355:	learn: 163.9663448	test: 195.3187216	best: 195.3187216 (355)	total: 19.5s	remaining: 4m 14s
356:	learn: 163.9031669	test: 195.2955632	best: 195.2955632 (356)	total: 19.6s	remaining: 4m 14s
357:	learn: 163.8424461	test: 195.2414816	best: 195.2414816 (357)	total: 19.6s	remaining: 4m 14s
358:	learn: 163.7841031	test: 195.2323955	best: 195.2323955 (358)	total: 19.7s	remaining: 4m 14s
359:	learn: 163.6283931	test: 195.1527925	best: 195.1527925 (359)	total: 19.7s	remaining: 4m 14s
360:	learn: 163.4402624	test: 195.0938617	best: 195.0938617 (360)	total: 19.8s	remaining: 4m 14s
361:	learn: 163.3534909	test: 

...

4585:	learn: 77.9680592	test: 178.1016786	best: 178.0870349 (4562)	total: 4m 38s	remaining: 25.1s
4586:	learn: 77.9638320	test: 178.1028731	best: 178.0870349 (4562)	total: 4m 38s	remaining: 25.1s
4587:	learn: 77.9398189	test: 178.1081399	best: 178.0870349 (4562)	total: 4m 38s	remaining: 25s
4588:	learn: 77.9381690	test: 178.1158151	best: 178.0870349 (4562)	total: 4m 38s	remaining: 24.9s
4589:	learn: 77.9266620	test: 178.1240314	best: 178.0870349 (4562)	total: 4m 38s	remaining: 24.9s
4590:	learn: 77.9173386	test: 178.1185349	best: 178.0870349 (4562)	total: 4m 38s	remaining: 24.8s
4591:	learn: 77.9106611	test: 178.1131853	best: 178.0870349 (4562)	total: 4m 38s	remaining: 24.7s
4592:	learn: 77.8889506	test: 178.1071941	best: 178.0870349 (4562)	total: 4m 38s	remaining: 24.7s
4593:	learn: 77.8826894	test: 178.1059583	best: 178.0870349 (4562)	total: 4m 38s	remaining: 24.6s
4594:	learn: 77.8663240	test: 178.0744600	best: 178.0744600 (4594)	total: 4m 38s	remaining: 24.6s
4595:	learn: 77.853806

4669:	learn: 77.3308318	test: 178.1165924	best: 178.0382301 (4601)	total: 4m 43s	remaining: 20s
4670:	learn: 77.3116441	test: 178.1139211	best: 178.0382301 (4601)	total: 4m 43s	remaining: 19.9s
4671:	learn: 77.3111663	test: 178.1120655	best: 178.0382301 (4601)	total: 4m 43s	remaining: 19.9s
4672:	learn: 77.3067568	test: 178.1068198	best: 178.0382301 (4601)	total: 4m 43s	remaining: 19.8s
4673:	learn: 77.3067047	test: 178.1064024	best: 178.0382301 (4601)	total: 4m 43s	remaining: 19.8s
4674:	learn: 77.3042344	test: 178.1082728	best: 178.0382301 (4601)	total: 4m 43s	remaining: 19.7s
4675:	learn: 77.3009811	test: 178.1034411	best: 178.0382301 (4601)	total: 4m 43s	remaining: 19.6s
4676:	learn: 77.2972531	test: 178.1087209	best: 178.0382301 (4601)	total: 4m 43s	remaining: 19.6s
4677:	learn: 77.2959803	test: 178.1060979	best: 178.0382301 (4601)	total: 4m 43s	remaining: 19.5s
4678:	learn: 77.2889693	test: 178.1137937	best: 178.0382301 (4601)	total: 4m 43s	remaining: 19.5s
4679:	learn: 77.287307

4753:	learn: 76.6476203	test: 177.9966325	best: 177.9844614 (4747)	total: 4m 47s	remaining: 14.9s
4754:	learn: 76.6451973	test: 177.9976096	best: 177.9844614 (4747)	total: 4m 47s	remaining: 14.8s
4755:	learn: 76.6383900	test: 178.0011002	best: 177.9844614 (4747)	total: 4m 48s	remaining: 14.8s
4756:	learn: 76.6373989	test: 178.0014814	best: 177.9844614 (4747)	total: 4m 48s	remaining: 14.7s
4757:	learn: 76.6307326	test: 178.0119696	best: 177.9844614 (4747)	total: 4m 48s	remaining: 14.7s
4758:	learn: 76.6281813	test: 178.0111500	best: 177.9844614 (4747)	total: 4m 48s	remaining: 14.6s
4759:	learn: 76.6275323	test: 178.0121334	best: 177.9844614 (4747)	total: 4m 48s	remaining: 14.5s
4760:	learn: 76.6272719	test: 178.0136124	best: 177.9844614 (4747)	total: 4m 48s	remaining: 14.5s
4761:	learn: 76.6194818	test: 178.0159463	best: 177.9844614 (4747)	total: 4m 48s	remaining: 14.4s
4762:	learn: 76.6161909	test: 178.0286095	best: 177.9844614 (4747)	total: 4m 48s	remaining: 14.4s
4763:	learn: 76.6080

4837:	learn: 76.1475110	test: 177.9557256	best: 177.9224009 (4811)	total: 4m 52s	remaining: 9.8s
4838:	learn: 76.1464400	test: 177.9576996	best: 177.9224009 (4811)	total: 4m 52s	remaining: 9.74s
4839:	learn: 76.1453963	test: 177.9550824	best: 177.9224009 (4811)	total: 4m 52s	remaining: 9.68s
4840:	learn: 76.1423986	test: 177.9575930	best: 177.9224009 (4811)	total: 4m 53s	remaining: 9.62s
4841:	learn: 76.1310667	test: 177.9608106	best: 177.9224009 (4811)	total: 4m 53s	remaining: 9.56s
4842:	learn: 76.1295829	test: 177.9568448	best: 177.9224009 (4811)	total: 4m 53s	remaining: 9.5s
4843:	learn: 76.1276775	test: 177.9459777	best: 177.9224009 (4811)	total: 4m 53s	remaining: 9.44s
4844:	learn: 76.1145539	test: 177.9264801	best: 177.9224009 (4811)	total: 4m 53s	remaining: 9.38s
4845:	learn: 76.1128873	test: 177.9273105	best: 177.9224009 (4811)	total: 4m 53s	remaining: 9.32s
4846:	learn: 76.1099513	test: 177.9314975	best: 177.9224009 (4811)	total: 4m 53s	remaining: 9.26s
4847:	learn: 76.105348

4924:	learn: 75.7802646	test: 177.8309954	best: 177.8309954 (4924)	total: 4m 57s	remaining: 4.54s
4925:	learn: 75.7791824	test: 177.8370426	best: 177.8309954 (4924)	total: 4m 57s	remaining: 4.47s
4926:	learn: 75.7647772	test: 177.8317981	best: 177.8309954 (4924)	total: 4m 57s	remaining: 4.41s
4927:	learn: 75.7609041	test: 177.8307464	best: 177.8307464 (4927)	total: 4m 57s	remaining: 4.35s
4928:	learn: 75.7303095	test: 177.8328584	best: 177.8307464 (4927)	total: 4m 58s	remaining: 4.29s
4929:	learn: 75.7234460	test: 177.8321520	best: 177.8307464 (4927)	total: 4m 58s	remaining: 4.23s
4930:	learn: 75.7188430	test: 177.8086626	best: 177.8086626 (4930)	total: 4m 58s	remaining: 4.17s
4931:	learn: 75.7133610	test: 177.8103903	best: 177.8086626 (4930)	total: 4m 58s	remaining: 4.11s
4932:	learn: 75.7084696	test: 177.8129747	best: 177.8086626 (4930)	total: 4m 58s	remaining: 4.05s
4933:	learn: 75.7072087	test: 177.8117156	best: 177.8086626 (4930)	total: 4m 58s	remaining: 3.99s
4934:	learn: 75.7049

In [12]:
print(vec_qual)
#model = pickle.load(open(input_dir + f'mod_part_feat_{i}.sav', 'rb'))

[230.53069459633494]


In [13]:
y_test

array([ 740.24322632, 1139.40816241,  183.82454798,  616.71590372,
         33.20229656,   79.77274634,  357.82626826,  116.4291483 ,
        361.38910193,  159.22548176,  500.79438056,   72.28912249,
         32.20720285,   42.89503947,  323.22053259,  746.25911517,
         21.19533664,   83.0954491 ,  223.93990081,  180.49097159,
        516.82213669,  296.9855674 ,  198.94044958,  324.82122126,
        180.9062582 ,  319.93780201,  324.83397777,  728.24524596,
         66.17322529,  184.95947211,  302.02759125,  128.57338089,
        136.43697377,    7.03960265,  167.54080366,  517.81143035,
         31.47402602,  121.7670198 ,  163.45532006,  304.33024208,
        268.96163667,   89.90792454,   25.96463781,  757.94272317,
        551.68813963, 1191.62578732,    0.        ,  499.95464848,
        148.0487076 ,  244.24964796,    7.4557219 ,  523.48977713,
        146.25627837,   57.05420028,   83.71983946,  117.51075502,
         81.54159574,   85.84222885,   56.14983965,  111.65145

In [14]:
test_data_may = test_data

In [15]:
test_data_may['value'] = list(y_test)

In [16]:
test_data_may

id                               bulk_id  spalen       date1  \
0      12  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-05-01   
1      13  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-05-01   
2      14  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-05-01   
3      15  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-05-01   
4      22  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-05-01   
5      91  72B1CAF6-A2DC-E511-9840-001EC9D56418       2  2018-05-01   
6      92  35168781-8F60-E611-9523-001EC9D5643C       3  2018-05-01   
7      93  35168781-8F60-E611-9523-001EC9D5643C       2  2018-05-01   
8      94  A8632090-8F60-E611-9523-001EC9D5643C       3  2018-05-01   
9      95  A8632090-8F60-E611-9523-001EC9D5643C       2  2018-05-01   
10     97  F4BE45B2-AFF2-E611-84D2-001EC9D56418       3  2018-05-01   
11     98  F4BE45B2-AFF2-E611-84D2-001EC9D56418       4  2018-05-01   
12     99  F4BE45B2-AFF2-E611-84D2-001EC9D56418       1  2018-05-01   
13    100  F4BE45B2-AFF2-E611-84D2-001EC9D56418       2  2018-05-01   
14    101  832FDFD6-AFF2-E611-84D2-001EC9D56418       3  2018-05-01   
15    102  832FDFD6-AFF2-E611-84D2-001EC9D56418       2  2018-05-01   
16    103  A93667C6-B147-E311-8507-001EC9D5643C       2  2018-05-01   
17    104  5C0E0157-C197-E711-8530-00505688958B       0  2018-05-01   
18    105  5C0E0157-C197-E711-8530-00505688958B       3  2018-05-01   
19    106  5C0E0157-C197-E711-8530-00505688958B       1  2018-05-01   
20    107  5C0E0157-C197-E711-8530-00505688958B       2  2018-05-01   
21    117  BC92BE33-C197-E711-8530-00505688958B       3  2018-05-01   
22    118  BC92BE33-C197-E711-8530-00505688958B       1  2018-05-01   
23    119  BC92BE33-C197-E711-8530-00505688958B       2  2018-05-01   
24    120  67127343-C197-E711-8530-00505688958B       1  2018-05-01   
25    121  67127343-C197-E711-8530-00505688958B       3  2018-05-01   
26    122  67127343-C197-E711-8530-00505688958B       2  2018-05-01   
27    127  BE6C758E-25F4-E611-84D2-001EC9D56418       2  2018-05-01   
28    128  BE6C758E-25F4-E611-84D2-001EC9D56418       1  2018-05-01   
29    157  D312086D-869A-E611-BE92-001EC9D5643C       1  2018-05-01   
..    ...                                   ...     ...         ...   
437  1743  51917AB1-4566-E711-97EC-001EC9D56418       2  2018-05-01   
438  1744  51917AB1-4566-E711-97EC-001EC9D56418       3  2018-05-01   
439  1745  9A2B12C5-4566-E711-97EC-001EC9D56418       3  2018-05-01   
440  1746  9A2B12C5-4566-E711-97EC-001EC9D56418       2  2018-05-01   
441  1747  9A2B12C5-4566-E711-97EC-001EC9D56418       1  2018-05-01   
442  1748  9A2B12C5-4566-E711-97EC-001EC9D56418       4  2018-05-01   
443  1749  9A2B12C5-4566-E711-97EC-001EC9D56418       0  2018-05-01   
444  1750  E51769DC-4566-E711-97EC-001EC9D56418       2  2018-05-01   
445  1751  E51769DC-4566-E711-97EC-001EC9D56418       1  2018-05-01   
446  1752  E51769DC-4566-E711-97EC-001EC9D56418       3  2018-05-01   
447  1753  E51769DC-4566-E711-97EC-001EC9D56418       4  2018-05-01   
448  1795  8CEB3310-63E8-E611-B887-001EC9D5643C       4  2018-05-01   
449  1796  8CEB3310-63E8-E611-B887-001EC9D5643C       2  2018-05-01   
450  1797  8CEB3310-63E8-E611-B887-001EC9D5643C       3  2018-05-01   
451  1798  8CEB3310-63E8-E611-B887-001EC9D5643C       1  2018-05-01   
452  1799  8CEB3310-63E8-E611-B887-001EC9D5643C       0  2018-05-01   
453  1801  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       2  2018-05-01   
454  1802  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       1  2018-05-01   
455  1804  C0B1362A-C378-E511-B4A4-001EC9D5643C       2  2018-05-01   
456  1805  C0B1362A-C378-E511-B4A4-001EC9D5643C       3  2018-05-01   
457  1807  C0B1362A-C378-E511-B4A4-001EC9D5643C       1  2018-05-01   
458  1808  999F708D-4FE9-E711-B9FF-00505688958B       0  2018-05-01   
459  1809  999F708D-4FE9-E711-B9FF-00505688958B       1  2018-05-01   
460  1810  999F708D-4FE9-E711-B9FF-00505688958B       2  2018-05-01   
461  1811  999F708D-4FE9-E711-B

#### Unload Data

In [17]:
test_data_may.to_csv(sub_dir + f"/subsub_full_feat_may.csv")